## Simple ETL pipeline in Databricks 

### Extract data from local : E of the ETL pipeline

In [0]:

# Define the file path (can be DBFS, S3, etc.)
file_path = "/FileStore/tables/forex.csv"

# Reading CSV file into a DataFrame
df = spark.read.format("csv") \
    .option("header", "true") \
    .option("inferSchema", "true") \
    .load(file_path)

# Show the DataFrame
display(df.limit(10))


slug date open high low close currency GBP/EGP 2001-04-10 5.5809 5.5947 5.5947 5.5947 EGP GBP/EGP 2001-06-04 5.47517 5.4939 5.4939 5.4939 EGP GBP/EGP 2001-08-01 5.6799 5.6543 5.6543 5.6543 EGP GBP/EGP 2002-07-29 7.217 7.217 7.217 7.217 EGP GBP/EGP 2003-01-02 7.42429 7.3899 7.3899 7.3899 EGP GBP/EGP 2003-04-21 9.29241 9.25045 9.25045 9.25045 EGP GBP/EGP 2004-02-13 11.607 11.642 11.52 11.578 EGP GBP/EGP 2004-02-16 11.571 11.623 11.499 11.607 EGP GBP/EGP 2004-02-17 11.608 11.739 11.521 11.662 EGP GBP/EGP 2004-02-18 11.677 11.772 11.631 11.691 EGP

#### Some checkings I gotta do

##### Check datatypes

In [0]:
print(df.dtypes)

[('slug', 'string'), ('date', 'date'), ('open', 'double'), ('high', 'double'), ('low', 'double'), ('close', 'double'), ('currency', 'string')]


##### Find the max and min date

In [0]:
df.createOrReplaceTempView('date_table')

# Run the SQL query
res = spark.sql("""
    SELECT YEAR(date) as year FROM date_table
""")
res.show(5)

+----+
|year|
+----+
|2001|
|2001|
|2001|
|2002|
|2003|
+----+
only showing top 5 rows



### Transforming the data : T of the ETL pipeline

#### Transformation # 1: Selecting only the last 5 years values

In [0]:
from pyspark.sql import functions as f

df.createOrReplaceTempView("newtable")

res1 = spark.sql("SELECT * FROM newtable WHERE YEAR(date) BETWEEN 2016 AND 2021")
display(res1)


slug date open high low close currency GBP/EGP 2016-01-01 11.371 11.503 11.371 11.371 EGP GBP/EGP 2016-01-04 11.376 11.562 11.371 11.373 EGP GBP/EGP 2016-01-05 11.49 11.505 11.429 11.49 EGP GBP/EGP 2016-01-06 11.458 11.461 11.399 11.453 EGP GBP/EGP 2016-01-07 11.419 11.434 11.348 11.42 EGP GBP/EGP 2016-01-08 11.414 11.432 11.342 11.416 EGP GBP/EGP 2016-01-11 11.105 11.398 11.098 11.102 EGP GBP/EGP 2016-01-12 11.353 11.372 11.204 11.351 EGP GBP/EGP 2016-01-13 11.274 11.311 11.233 11.273 EGP GBP/EGP 2016-01-14 11.247 11.271 11.208 11.245 EGP GBP/EGP 2016-01-15 11.259 11.261 11.169 11.259 EGP GBP/EGP 2016-01-18 10.961 11.185 10.946 10.958 EGP GBP/EGP 2016-01-19 11.128 11.197 11.027 11.128 EGP GBP/EGP 2016-01-20 11.064 11.103 11.028 11.067 EGP GBP/EGP 2016-01-21 11.088 11.091 10.994 11.082 EGP GBP/EGP 2016-01-22 11.106 11.216 11.086 11.111 EGP GBP/EGP 2016-01-25 11.128 11.173 11.004 11.128 EGP GBP/EGP 2016-01-26 11.113 11.186 11.064 11.113 EGP GBP/EGP 2016-01-27 11.198 11.21 11.112 11.198 EGP GBP/EGP 2016-01-28 11.124 11.242 11.114 11.122 EGP GBP/EGP 2016-01-29 11.216 11.255 11.086 11.216 EGP GBP/EGP 2016-02-01 11.049 11.229 11.029 11.046 EGP GBP/EGP 2016-02-02 11.263 11.274 11.185 11.263 EGP GBP/EGP 2016-02-03 11.249 11.392 11.226 11.254 EGP GBP/EGP 2016-02-04 11.382 11.453 11.345 11.384 EGP GBP/EGP 2016-02-05 11.384 11.388 11.29 11.384 EGP GBP/EGP 2016-02-08 11.344 11.366 11.213 11.345 EGP GBP/EGP 2016-02-09 11.268 11.307 11.226 11.267 EGP GBP/EGP 2016-02-10 11.289 11.382 11.28 11.292 EGP GBP/EGP 2016-02-11 11.338 11.374 11.227 11.339 EGP GBP/EGP 2016-02-12 11.303 11.377 11.279 11.304 EGP GBP/EGP 2016-02-15 11.228 11.356 11.207 11.224 EGP GBP/EGP 2016-02-16 11.277 11.326 11.147 11.28 EGP GBP/EGP 2016-02-17 11.171 11.195 11.109 11.168 EGP GBP/EGP 2016-02-18 11.154 11.236 11.139 11.154 EGP GBP/EGP 2016-02-19 11.188 11.203 11.123 11.186 EGP GBP/EGP 2016-02-22 10.955 11.164 10.955 10.956 EGP GBP/EGP 2016-02-23 11.046 11.051 10.984 11.044 EGP GBP/EGP 2016-02-24 10.933 10.946 10.834 10.935 EGP GBP/EGP 2016-02-25 10.875 10.929 10.851 10.878 EGP GBP/EGP 2016-02-26 10.898 10.954 10.823 10.898 EGP GBP/EGP 2016-02-29 10.762 10.888 10.745 10.76 EGP GBP/EGP 2016-03-01 10.872 10.938 10.86 10.872 EGP GBP/EGP 2016-03-02 10.895 10.986 10.859 10.898 EGP GBP/EGP 2016-03-03 10.99 11.055 10.96 10.988 EGP GBP/EGP 2016-03-04 11.067 11.111 11.017 11.064 EGP GBP/EGP 2016-03-07 10.922 11.116 10.918 10.926 EGP GBP/EGP 2016-03-08 11.133 11.14 11.064 11.134 EGP GBP/EGP 2016-03-09 11.085 11.126 11.067 11.087 EGP GBP/EGP 2016-03-10 11.093 11.165 11.023 11.094 EGP GBP/EGP 2016-03-11 11.155 11.235 11.128 11.155 EGP GBP/EGP 2016-03-14 11.005 12.836 11.005 11.004 EGP GBP/EGP 2016-03-15 12.749 12.755 12.623 12.749 EGP GBP/EGP 2016-03-16 12.635 12.638 12.467 12.636 EGP GBP/EGP 2016-03-17 12.618 12.837 12.593 12.619 EGP GBP/EGP 2016-03-18 12.824 12.85 12.767 12.822 EGP GBP/EGP 2016-03-21 12.802 12.802 12.721 12.806 EGP GBP/EGP 2016-03-22 12.729 12.754 12.578 12.728 EGP GBP/EGP 2016-03-23 12.598 12.602 12.363 12.598 EGP GBP/EGP 2016-03-24 12.505 12.568 12.336 12.504 EGP GBP/EGP 2016-03-25 12.534 12.541 12.331 12.534 EGP GBP/EGP 2016-03-28 12.539 12.545 12.353 12.54 EGP GBP/EGP 2016-03-29 12.608 12.67 12.584 12.609 EGP GBP/EGP 2016-03-30 12.736 12.807 12.602 12.74 EGP GBP/EGP 2016-03-31 12.731 12.775 12.691 12.731 EGP GBP/EGP 2016-04-01 12.726 12.732 12.55 12.726 EGP GBP/EGP 2016-04-04 12.599 12.681 12.516 12.604 EGP GBP/EGP 2016-04-05 12.634 12.648 12.512 12.637 EGP GBP/EGP 2016-04-06 12.543 12.552 12.411 12.542 EGP GBP/EGP 2016-04-07 12.518 12.536 12.444 12.516 EGP GBP/EGP 2016-04-08 12.454 12.521 12.441 12.454 EGP GBP/EGP 2016-04-11 12.51 12.643 12.457 12.512 EGP GBP/EGP 2016-04-12 12.609 12.706 12.573 12.608 EGP GBP/EGP 2016-04-13 12.638 12.651 12.577 12.635 EGP GBP/EGP 2016-04-14 12.564 12.568 12.396 12.567 EGP GBP/EGP 2016-04-15 12.525 12.591 12.519 12.522 EGP GBP/EGP 2016-04-18 12.551 12.656 12.409 12.543 EGP GBP/EGP 2016-04-19 12.654 12.77 12.652 12.659 EGP GB

#### Transformation # 2: Finding out the day of the week for each closing stock

In [0]:
res1 = df.withColumn("weekday", f.date_format("date", "EEEE"))
display(res1)

slug date open high low close currency weekday GBP/EGP 2001-04-10 5.5809 5.5947 5.5947 5.5947 EGP Tuesday GBP/EGP 2001-06-04 5.47517 5.4939 5.4939 5.4939 EGP Monday GBP/EGP 2001-08-01 5.6799 5.6543 5.6543 5.6543 EGP Wednesday GBP/EGP 2002-07-29 7.217 7.217 7.217 7.217 EGP Monday GBP/EGP 2003-01-02 7.42429 7.3899 7.3899 7.3899 EGP Thursday GBP/EGP 2003-04-21 9.29241 9.25045 9.25045 9.25045 EGP Monday GBP/EGP 2004-02-13 11.607 11.642 11.52 11.578 EGP Friday GBP/EGP 2004-02-16 11.571 11.623 11.499 11.607 EGP Monday GBP/EGP 2004-02-17 11.608 11.739 11.521 11.662 EGP Tuesday GBP/EGP 2004-02-18 11.677 11.772 11.631 11.691 EGP Wednesday GBP/EGP 2004-02-19 11.691 11.705 11.522 11.603 EGP Thursday GBP/EGP 2004-02-20 11.603 11.644 11.3878 11.463 EGP Friday GBP/EGP 2004-02-23 11.469 11.514 11.3185 11.503 EGP Monday GBP/EGP 2004-02-24 11.502 11.6382 11.389 11.611 EGP Tuesday GBP/EGP 2004-02-25 11.612 11.6481 11.4961 11.52 EGP Wednesday GBP/EGP 2004-02-26 11.521 11.5453 11.408 11.459 EGP Thursday GBP/EGP 2004-02-27 11.459 11.4895 11.3603 11.459 EGP Friday GBP/EGP 2004-03-01 11.444 11.527 11.423 11.48 EGP Monday GBP/EGP 2004-03-02 11.481 11.4969 11.2872 11.317 EGP Tuesday GBP/EGP 2004-03-03 11.319 11.33 11.153 11.155 EGP Wednesday GBP/EGP 2004-03-04 11.158 11.3128 11.155 11.199 EGP Thursday GBP/EGP 2004-03-05 11.199 11.3898 11.146 11.354 EGP Friday GBP/EGP 2004-03-08 11.359 11.4212 11.314 11.344 EGP Monday GBP/EGP 2004-03-09 11.344 11.4446 11.2296 11.323 EGP Tuesday GBP/EGP 2004-03-10 11.344 11.4446 11.0719 11.087 EGP Wednesday GBP/EGP 2004-03-11 11.083 11.1754 10.988 11.058 EGP Thursday GBP/EGP 2004-03-12 11.056 11.1514 11.018 11.066 EGP Friday GBP/EGP 2004-03-15 11.043 11.1752 11.028 11.075 EGP Monday GBP/EGP 2004-03-16 11.074 11.2245 11.066 11.1869 EGP Tuesday GBP/EGP 2004-03-17 11.14 11.2159 11.075 11.14 EGP Wednesday GBP/EGP 2004-03-18 11.146 11.3436 11.141 11.286 EGP Thursday GBP/EGP 2004-03-19 11.29 11.3306 11.255 11.283 EGP Friday GBP/EGP 2004-03-22 11.289 11.4102 11.222 11.387 EGP Monday GBP/EGP 2004-03-23 11.388 11.4362 11.288 11.366 EGP Tuesday GBP/EGP 2004-03-24 11.368 11.4368 11.208 11.324 EGP Wednesday GBP/EGP 2004-03-25 11.322 11.333 11.033 11.191 EGP Thursday GBP/EGP 2004-03-26 11.193 11.2424 11.1085 11.169 EGP Friday GBP/EGP 2004-03-29 11.164 11.2116 11.09 11.178 EGP Monday GBP/EGP 2004-03-30 11.177 11.289 11.13 11.24 EGP Tuesday GBP/EGP 2004-03-31 11.236 11.352 11.217 11.317 EGP Wednesday GBP/EGP 2004-04-01 11.321 11.445 11.225 11.378 EGP Thursday GBP/EGP 2004-04-02 11.374 11.409 11.061 11.245 EGP Friday GBP/EGP 2004-04-05 11.263 11.279 11.103 11.161 EGP Monday GBP/EGP 2004-04-06 11.159 11.349 11.117 11.321 EGP Tuesday GBP/EGP 2004-04-07 11.32 11.365 11.206 11.277 EGP Wednesday GBP/EGP 2004-04-08 11.276 11.407 11.216 11.224 EGP Thursday GBP/EGP 2004-04-09 11.223 11.241 11.207 11.234 EGP Friday GBP/EGP 2004-04-12 11.232 11.285 11.23 11.275 EGP Monday GBP/EGP 2004-04-13 11.274 11.317 11.126 11.155 EGP Tuesday GBP/EGP 2004-04-14 11.161 11.195 10.979 11.033 EGP Wednesday GBP/EGP 2004-04-15 11.03 11.086 10.888 10.975 EGP Thursday GBP/EGP 2004-04-16 10.977 11.15 10.941 11.097 EGP Friday GBP/EGP 2004-04-19 11.095 11.227 11.013 11.156 EGP Monday GBP/EGP 2004-04-20 10.977 11.175 10.941 11.06 EGP Tuesday GBP/EGP 2004-04-21 11.056 11.068 10.835 10.924 EGP Wednesday GBP/EGP 2004-04-22 10.926 10.929 10.822 10.834 EGP Thursday GBP/EGP 2004-04-23 10.832 10.9532 10.818 10.824 EGP Friday GBP/EGP 2004-04-26 10.868 11.0099 10.859 10.971 EGP Monday GBP/EGP 2004-04-27 10.98 11.017 10.9206 11.005 EGP Tuesday GBP/EGP 2004-04-28 11.008 11.02 10.8343 10.869 EGP Wednesday GBP/EGP 2004-04-29 10.871 10.94 10.7609 10.91 EGP Thursday GBP/EGP 2004-04-30 10.911 10.956 10.8104 10.948 EGP Friday GBP/EGP 2004-05-03 10.943 10.949 10.8263 10.903 EGP Monday GBP/EGP 2004-05-04 10.903 11.044 10.823 11.034 EGP Tuesday GBP/EGP 2004-05-05 11.033 11.038 10.9396 10.977 EGP Wednesday GBP/EGP 2004-05-06 10.98 11.039 10.9445 11.008 EGP Thursday GBP/EGP 2004-05-07 11.01 

In [0]:
# Calculate 7-day moving average for 'close' price
from pyspark.sql.window import Window

window_spec = Window.partitionBy("slug").orderBy("date").rowsBetween(-6, 0)  # 7-day window
res1 = res1.withColumn("7 day average", f.round(f.avg("close").over(window_spec), 3))

display(res1)

slug date open high low close currency weekday 7 day average AUD/EUR 2003-12-01 0.60121 0.60827 0.60121 0.60798 EUR Monday 0.608 AUD/EUR 2003-12-02 0.60772 0.60901 0.60379 0.60551 EUR Tuesday 0.607 AUD/EUR 2003-12-03 0.60558 0.60887 0.60459 0.60764 EUR Wednesday 0.607 AUD/EUR 2003-12-04 0.60779 0.61002 0.60588 0.60838 EUR Thursday 0.607 AUD/EUR 2003-12-05 0.60853 0.60872 0.60295 0.60419 EUR Friday 0.607 AUD/EUR 2003-12-08 0.60441 0.60779 0.60441 0.60544 EUR Monday 0.607 AUD/EUR 2003-12-09 0.60529 0.60584 0.6035 0.60397 EUR Tuesday 0.606 AUD/EUR 2003-12-10 0.60386 0.60687 0.60292 0.6054 EUR Wednesday 0.606 AUD/EUR 2003-12-11 0.60569 0.60624 0.60299 0.60489 EUR Thursday 0.606 AUD/EUR 2003-12-12 0.60492 0.60661 0.60245 0.60361 EUR Friday 0.605 AUD/EUR 2003-12-15 0.6058 0.60646 0.60339 0.60339 EUR Monday 0.604 AUD/EUR 2003-12-16 0.60361 0.60397 0.60201 0.6027 EUR Tuesday 0.604 AUD/EUR 2003-12-17 0.60295 0.60343 0.59404 0.59563 EUR Wednesday 0.603 AUD/EUR 2003-12-18 0.59559 0.59841 0.5927 0.59588 EUR Thursday 0.602 AUD/EUR 2003-12-19 0.59588 0.5963 0.59312 0.59446 EUR Friday 0.6 AUD/EUR 2003-12-22 0.59316 0.59379 0.59001 0.59193 EUR Monday 0.598 AUD/EUR 2003-12-23 0.59203 0.61275 0.59098 0.59488 EUR Tuesday 0.597 AUD/EUR 2003-12-24 0.59495 0.59751 0.59446 0.59577 EUR Wednesday 0.596 AUD/EUR 2003-12-25 0.59573 0.59652 0.59485 0.59623 EUR Thursday 0.595 AUD/EUR 2003-12-26 0.59623 0.59748 0.59531 0.59705 EUR Friday 0.595 AUD/EUR 2003-12-29 0.59613 0.59677 0.59365 0.59517 EUR Monday 0.595 AUD/EUR 2003-12-30 0.59538 0.59784 0.59506 0.59648 EUR Tuesday 0.595 AUD/EUR 2003-12-31 0.59627 0.59859 0.59404 0.59666 EUR Wednesday 0.596 AUD/EUR 2004-01-01 0.59748 0.60306 0.59666 0.5978 EUR Thursday 0.596 AUD/EUR 2004-01-02 0.59773 0.60328 0.59673 0.60314 EUR Friday 0.598 AUD/EUR 2004-01-05 0.60107 0.60646 0.6002 0.60467 EUR Monday 0.599 AUD/EUR 2004-01-06 0.60452 0.60669 0.6023 0.6035 EUR Tuesday 0.6 AUD/EUR 2004-01-07 0.60405 0.60805 0.60226 0.60728 EUR Wednesday 0.601 AUD/EUR 2004-01-08 0.6072 0.61035 0.60584 0.60606 EUR Thursday 0.603 AUD/EUR 2004-01-09 0.60632 0.60879 0.60288 0.60314 EUR Friday 0.604 AUD/EUR 2004-01-12 0.60492 0.61039 0.60368 0.60909 EUR Monday 0.605 AUD/EUR 2004-01-13 0.60931 0.61185 0.60879 0.60953 EUR Tuesday 0.606 AUD/EUR 2004-01-14 0.60994 0.61455 0.59513 0.61166 EUR Wednesday 0.607 AUD/EUR 2004-01-15 0.61173 0.61316 0.60998 0.61211 EUR Thursday 0.608 AUD/EUR 2004-01-16 0.61218 0.61824 0.61117 0.61538 EUR Friday 0.61 AUD/EUR 2004-01-19 0.61414 0.61448 0.6082 0.61043 EUR Monday 0.61 AUD/EUR 2004-01-20 0.61061 0.61271 0.60901 0.60964 EUR Tuesday 0.611 AUD/EUR 2004-01-21 0.60964 0.61444 0.60953 0.61095 EUR Wednesday 0.611 AUD/EUR 2004-01-22 0.61102 0.61335 0.60827 0.61102 EUR Thursday 0.612 AUD/EUR 2004-01-23 0.61099 0.61365 0.60887 0.61252 EUR Friday 0.612 AUD/EUR 2004-01-26 0.61323 0.61786 0.61301 0.61576 EUR Monday 0.612 AUD/EUR 2004-01-27 0.61599 0.61969 0.6152 0.61603 EUR Tuesday 0.612 AUD/EUR 2004-01-28 0.61599 0.61939 0.61512 0.61839 EUR Wednesday 0.613 AUD/EUR 2004-01-29 0.61847 0.61939 0.61143 0.61357 EUR Thursday 0.614 AUD/EUR 2004-01-30 0.61346 0.61592 0.60909 0.61155 EUR Friday 0.614 AUD/EUR 2004-02-02 0.61267 0.61342 0.60794 0.60994 EUR Monday 0.614 AUD/EUR 2004-02-03 0.60739 0.60968 0.60646 0.60753 EUR Tuesday 0.613 AUD/EUR 2004-02-04 0.60753 0.60968 0.60646 0.60731 EUR Wednesday 0.612 AUD/EUR 2004-02-05 0.60739 0.60805 0.60558 0.60643 EUR Thursday 0.611 AUD/EUR 2004-02-06 0.60624 0.6089 0.60397 0.60573 EUR Friday 0.609 AUD/EUR 2004-02-09 0.6058 0.61256 0.6058 0.61151 EUR Monday 0.609 AUD/EUR 2004-02-10 0.61185 0.61576 0.6105 0.61482 EUR Tuesday 0.609 AUD/EUR 2004-02-11 0.61489 0.61527 0.61188 0.61323 EUR Wednesday 0.61 AUD/EUR 2004-02-12 0.61338 0.61671 0.61248 0.61565 EUR Thursday 0.611 AUD/EUR 2004-02-13 0.6155 0.62073 0.61512 0.6205 EUR Friday 0.613 AUD/EUR 2004-02-16 0.62108 0.62154 0.61912 0.62 EUR Monday 0.614 AUD/EUR 2004-02-17 0.61992 0.62201 0.6187 0.62027 EUR Tuesday 0.617 AUD/EUR 2004-02-18 0.61981

### Loading / Writing to the Filestore : L of the ETL

In [0]:
df.write.format('csv').option('header','true').save('/FileStore/tables/newforex.csv')